In [63]:
from numpy import arange
from pandas import read_csv
from scipy.optimize import curve_fit
from matplotlib import pyplot
import numpy as np
import scipy
from scipy.integrate import quad
import warnings
import matplotlib.pyplot as plt
import pandas as pd
import math
from scipy.stats import gamma
from scipy.stats import beta
from sklearn.preprocessing import normalize
from contextlib import suppress

def Error(y_true, y_predicted): #Barnston, 1992):
    """
    - y_true: Actual values
    - y_predicted: Predicted values
    """
    y_true = np.array(y_true)
    y_predicted = np.array(y_predicted)
    
    #RMSE
    RSS = np.sum(np.square(y_true - y_predicted))
    rmse = math.sqrt(RSS / len(y_true)) 
    
    #MASE When comparing forecasting methods, the method with the lowest MASE is the preferred method. 
    error = np.sum(np.abs(y_true-y_predicted))/ len(y_true)
    error2 = np.sum(np.abs(y_true-np.mean(y_true)))/ len(y_true)
    MASE= error/error2
    
    return rmse,MASE  

def gamma_cumulative(x,a,scale=1):
    loc=0
    return gamma.cdf(x,a,loc,scale)
def rho_gamma(x,a,scale=1):
    loc=0
    return gamma.pdf(x,a,loc,scale)

def beta_cumulative(x,a,b,scale=1):
    loc=0
    return beta.cdf(x,a,b,loc,scale)
def rho_beta(x,a,b,scale=1):
    loc=0
    return beta.pdf(x,a,b,loc,scale)

def frechet(x,a,s):
    return np.exp(-((x/s)**(-a)))
def rho_frechet(x,a,s,offset=0):
    return (a/s)*((x/s)**(-(a+1)))*np.exp(-((x/s)**(-a)))

def normal(x, sigma_normal, mue_normal):
    return 0.5*(1+scipy.special.erf((x-mue_normal)/np.sqrt(2*sigma_normal**2)))
def rho_normal(x, sigma_normal, mue_normal):
    return (1/np.sqrt(2*np.pi*sigma_normal**2))*np.exp(-(((x-mue_normal)**2)/(2*sigma_normal**2)))

def weibul(x, n_weibul, a_weibul):   #a = k ; n = lambda
    return 1-np.exp(-(x / n_weibul)**a_weibul)
def rho_weibul(x,n,a):
    return (a / n) * (x / n)**(a - 1) * np.exp(-(x / n)**a)

def lognormal(x, sigma_lognormal, mue_lognormal):
    return (0.5*(1+scipy.special.erf((x-mue_lognormal)/np.sqrt(2*sigma_lognormal**2))))*((np.log(x)-mue_lognormal)/sigma_lognormal)
def rho_lognormal(x, sigma_lognormal, mue_lognormal):
    return (1/(np.sqrt(2*np.pi)*sigma_lognormal*x))*np.exp(-((np.log(x)-mue_lognormal)**2)/(2*sigma_lognormal**2))

def fit_distribution(x, y, dist_type='Normal',density_dist=False, plot=False):
    if dist_type == 'Normal':
        func = normal
        rho = rho_normal
    elif dist_type == 'Weibul':
        func = weibul
        rho = rho_weibul
    elif dist_type == 'Lognormal':
        func = lognormal
        rho = rho_lognormal
    elif dist_type == 'Gamma':
        func = gamma_cumulative
        rho = rho_gamma
    elif dist_type == 'Frechet':
        func = frechet
        rho = rho_frechet
    else:
        raise Exception('Invalid distribution type specified')
    if density_dist : 
        popt, __ = curve_fit(rho, x, y)
        y_pred = rho(x, *popt)
        rmse, mase = Error(y, y_pred)
    else:
        popt, __ = curve_fit(func, x, y)
        y_pred = func(x, *popt)
        rmse, mase = Error(y, y_pred)
    if plot:
        fig, axs = pyplot.subplots(2)
        fig.suptitle(dist_type+'-Verteilung')
        x_axis = np.linspace(min(x), max(x), len(x)*30)
        y_axis = rho(x_axis, *popt)
        y_axis1 = func(x_axis, *popt)
        if density_dist : 
            axs[1].scatter(x, y)
        else:
            axs[0].scatter(x, y)
        axs[0].plot(x_axis, y_axis1, '--', color='blue')
        axs[0].set_title('Verteilungskurve')
        axs[0].tick_params('x', labelbottom=False)
        axs[1].plot(x_axis, y_axis, '--', color='red')
        axs[1].set_title('Dichteverteilungskurve')
    return popt, rmse, mase


def bestfit_Auswahl(x,y,dist_data,plot=False):
    try:
        [sigma_lognormal, mue_lognormal], rse_logn, MASE_logn = fit_distribution(x, y, dist_type='Lognormal')
    except:
        [sigma_lognormal, mue_lognormal], rse_logn, MASE_logn =[1,1],10000,10000
    try:
        [n_weibul, a_weibul], rse_weibul, MASE_weibul         = fit_distribution(x, y, dist_type='Weibul')
    except:
        [n_weibul, a_weibul], rse_weibul, MASE_weibul   = [1,1],10000,10000
    try:
        [sigma_normal, mue_normal], rse_normal, MASE_normal   = fit_distribution(x, y, dist_type='Normal')
    except:
        [sigma_normal, mue_normal], rse_normal, MASE_normal   = [1,1],10000,10000
    try:
        [a_gamma, shape_gamma], rse_gamma, MASE_gamma         = fit_distribution(x, y, dist_type='Gamma')
    except:
        [a_gamma, shape_gamma], rse_gamma, MASE_gamma         =[1,1],10000,10000
    try:
        [a_frechet, shape_frechet], rse_frechet, MASE_frechet = fit_distribution(x, y, dist_type='Frechet')
    except:
        [a_frechet, shape_frechet], rse_frechet, MASE_frechet =[1,1],10000,10000
    Table= pd.DataFrame([[rse_weibul,rse_normal,rse_logn, rse_gamma, rse_frechet],[MASE_weibul,MASE_normal,MASE_logn,MASE_gamma,MASE_frechet],[n_weibul,0,0,0,0],
                         [a_weibul,0,0,0,0],[0,sigma_normal,sigma_lognormal,0,0],[0,mue_normal,mue_lognormal,0,0],[0,0,0,a_gamma,a_frechet],[0,0,0,shape_gamma,shape_frechet]], 
                        columns=['Weibul','Normal','Lognormal','Gamma','Frechet'], index=['RMSE','MASE','n_weibul','a_weibul','sigma','mue','a','shape',])
    Table1= pd.DataFrame([[rse_weibul,rse_normal,rse_logn,  rse_gamma, rse_frechet],[MASE_weibul,MASE_normal,MASE_logn,MASE_gamma,MASE_frechet]],
                        columns=['Weibul','Normal','Lognormal','Gamma','Frechet'], index=['RMSE','MASE'])
 
    Bestchoice=Table1.idxmin(axis="columns")
    if True: 
        print('Choice for '+str(Bestchoice[0])+'-distribution based on RMSE')
        output = Table[str(Bestchoice[0])]
        output = pd.DataFrame(output)
        output = output.drop(index='RMSE')
        output = output.drop(index='MASE')
        output = output.loc[~(output==0).all(axis=1)]
    else: 
#         output = Table
#         if True:#plot==False:
#             fit_distribution(x, y, dist_type=str(Bestchoice[0]),density_dist=density_dist, plot=True)
#             fit_distribution(x, y, dist_type=str(Bestchoice[1]),density_dist=density_dist, plot=True)
        print(Table[str(Bestchoice[0])])
        print(Table[str(Bestchoice[1])])
        answer=input('Choose between the '+str(Bestchoice[0])+ ' and '+str(Bestchoice[1])+ ' distribution: ')
        if str(answer)==str(Bestchoice[0]):
            output = Table[str(Bestchoice[0])]
            output = pd.DataFrame(output)
            output = output.drop(index='RMSE')
            output = output.drop(index='MASE')
            output = output.loc[~(output==0).all(axis=1)]
        elif str(answer)==str(Bestchoice[1]):
            output = Table[str(Bestchoice[1])]
            output = pd.DataFrame(output)
            output = output.drop(index='RMSE')
            output = output.drop(index='MASE')
            output = output.loc[~(output==0).all(axis=1)]
        else:
            print('you are an idiot xD')
            
    #Table.loc['MASE'].style.highlight_min(color = 'red', axis=1)
    if plot:
        plot_it(x,y,output.columns[0],output.values[0,0],output.values[1,0],dist_data)
    return output #, Table

def preprocessing(dist_data,ncol,classsize=None):
    disasterlvl1 = pd.read_csv(open(dist_data))
    l= np.arange(0,ncol,1)/100
    final=[]
    if disasterlvl1.index.stop<2:
        y1=disasterlvl1.iloc[0].to_numpy().ravel()
        y1_cdf=[]
        if 'Frank' in dist_data or 'Ruhl'in dist_data:    
            for j in range(len(y1)):
                cdf=y1[:(j+1)].sum()
                y1_cdf=np.append(y1_cdf,cdf)
        elif classsize is not None:    
            classsize=classsize
            y1_cdf=y1            
        else:
            raise Exception('please provide categorization of data')
        y2=bestfit_Auswahl(classsize,y1_cdf,dist_data,False)
        karl=(y2.columns[0],y2.values[0,0],y2.values[1,0])
        final.append(karl)

    else:
        k=disasterlvl1.columns.to_numpy()
        fraktions=disasterlvl1.index.stop
        l= np.linspace((ncol/fraktions), ncol, int(fraktions))/100
        for i in range(len(k)):
            with suppress(RuntimeError):
                y1=disasterlvl1.iloc[:,i].to_numpy()
                y1_cdf=[]
                karl=()
                for j in range(len(y1)):
                    cdf=y1[:(j+1)].sum()
                    y1_cdf=np.append(y1_cdf,cdf)
                y2=bestfit_Auswahl(l,y1_cdf,dist_data,False)
                karl=(y2.columns[0],y2.values[0,0],y2.values[1,0])
                final.append(karl)
    return final

def modelinput(dist_type, a,b,classvalue):
    if dist_type == 'Normal':
        func = normal
        rho = rho_normal
    elif dist_type == 'Weibul':
        func = weibul
        rho = rho_weibul
    elif dist_type == 'Lognormal':
        func = lognormal
        rho = rho_lognormal
    elif dist_type == 'Gamma':
        func = gamma_cumulative
        rho = rho_gamma
    elif dist_type == 'Frechet':
        func = frechet
        rho = rho_frechet
    else:
        raise Exception('Invalid distribution type specified')

    cdf=[]
    for i in range(len(classvalue)):
        if i==0:
            cdf=np.append(cdf, func(classvalue[i],a,b))
        else:
            cdf=np.append(cdf, func(classvalue[i],a,b)-func(classvalue[i-1],a,b))

    return cdf

def forvolfrac(dist_parameters,dist_data, classsize=None ):
    if classsize is not None:    
        classsize=classsize
    else:
        raise Exception('please provide categorization of data')
        
    if 'GroeßenVerteilung' in dist_data:
        x=0.01
        d1= modelinput(dist_parameters[0][0],dist_parameters[0][1],dist_parameters[0][2],[1.1])
        y=0
        while round(y,3) !=0.5:
            x+=0.0001
            y=modelinput(dist_parameters[0][0],dist_parameters[0][1],dist_parameters[0][2],[x])[0]
        d50= modelinput(dist_parameters[0][0],dist_parameters[0][1],dist_parameters[0][2],[x])
        print('d50 diameter for the experimental data is d50='+str(x))
        delta_x=1.1-x
        classsize_new =[]
        for i in range(len(classsize)):
            classsize_new.append(classsize[i]-(delta_x))
        predata= modelinput(dist_parameters[0][0],dist_parameters[0][1],dist_parameters[0][2],classsize_new)
        #fitting of d50 from data to arteficial value d50=1.1
        #plot_it(classsize,[delta_x],dist_parameters[0][0],dist_parameters[0][1],dist_parameters[0][2],'Adjusted to d50')
    else:
        predata= modelinput(dist_parameters[0][0],dist_parameters[0][1],dist_parameters[0][2],classsize)
    
    return predata
def plot_it(x,y,dist_type,a,b,name):
    if dist_type == 'Normal':
        func = normal
        rho = rho_normal
    elif dist_type == 'Weibul':
        func = weibul
        rho = rho_weibul
    elif dist_type == 'Lognormal':
        func = lognormal
        rho = rho_lognormal
    elif dist_type == 'Gamma':
        func = gamma_cumulative
        rho = rho_gamma
    elif dist_type == 'Frechet':
        func = frechet
        rho = rho_frechet
    x_axis = np.linspace(min(x), max(x), len(x)*30)
    y_axis = rho(x_axis, a,b)
    y_axis1 = func(x_axis, a,b)
    if len(y)>1:
        fig, axs = pyplot.subplots(2)
        fig.suptitle(name)
        axs[0].scatter(x, y)
        axs[0].plot(x_axis, y_axis1, '--', color='blue')
        axs[0].set_title(dist_type+'-distribution curve')
        axs[0].tick_params('x', labelbottom=False)
        axs[1].plot(x_axis, y_axis, '--', color='red')
        axs[1].set_title('Density distribution curve')
    else:
        x_axis1=[]
        for k in range(len(x_axis)):
            x_axis1.append(x_axis[k]-y[0])
        y_axis1 = rho(x_axis1, a,b)
        pyplot.plot(x_axis, y_axis1, '-', color='green')
        pyplot.title(name)
    
   
def vol_frac_input(ncol,npartype,rho_dichte=None,par_dichte=None,ax_par1=None,ax_distr=None,poroclass=None,sizeclass=None):
    # par_dichte ist ein Array mit der Dichtewerten der Partikelgrößenklassen
    size=np.zeros((ncol,npartype))
    def laengsverteilung (size,rho=1,rho_class=0):
        l= np.arange(0.1,ncol+0.1,1)/100
        #size=np.zeros((ncol,npartype))
        #print(size)
        for j in range(len(ax_par1)):
            boom = modelinput(ax_par1[j][0] ,ax_par1[j][1] ,ax_par1[j][2] ,l)
            boal  = boom.reshape(-1,1)
            checksum_col = np.sum(boal)
            bow= boal/checksum_col
            size[:,(len(ax_par1)*rho_class)+j] = bow[:,0]*rho*par_dichte[j]   #np.r_[size,bow]#np.hstack(bow)
        #size=size*par_dichte
        return size
    def vertical_simplifcation(ncol,npartype,rho_dichte=[1],par_dichte=[1],poroclass=[0],sizeclass=[0]):
        sectionlength = np.empty(npartype)
        for k in range(len(rho_dichte)):
            for i in range(len(par_dichte)):
                sectionlength[i+k*len(par_dichte)]=max(round(rho_dichte[k]*par_dichte[i]*ncol),1)
        sectionlength_total= np.empty(npartype)
        for j in range(len(sectionlength)):
            total=sectionlength[:(j+1)].sum()
            sectionlength_total[j]=total 
        rho_sep=len(poroclass)
        par_sep=len(sizeclass)
        size = np.zeros((ncol,npartype))
        counter=0
        section = 0
        for i in range(ncol):
            size[i,section] = 1
            if (i+1) % sectionlength_total[counter] == 0 and section < npartype-1 and i > 0:
                section +=1
                counter +=1
        if rho_sep>1 and par_sep>1:
            v_sed=np.zeros((ncol,npartype))
            def sedimentationvelocity(d_particle,porosity_par):
                """
                - d_particle in m 
                - Sedimentation in Stokes flow Re<<1 with ideal spherical particles
                """
                #d_particle in m
                rho_fluid=1000 #kg/m³ Water
                g = 9.81 # m/s²
                rho_material= 1600 #kg/m³ GAC might be adjusted
                nue_fluid=1.14e-3 #Pa*s Water at 15°C
                d_particle=d_particle/1000   # change unit from mm to m
                return ((g*(d_particle**2))/(nue_fluid*18))* ((1-porosity_par)*rho_material+(porosity_par-1)*rho_fluid) 
            for j in range(ncol):
                for i in range(len(sizeclass)):
                    v_sed[j,i]=sedimentationvelocity(sizeclass[i],poroclass[i])
            size=v_sed*size
            def sum_sort(row):  
                return sum(row)
            b=np.array(sorted(size,key=lambda row: sum(row)))
            size = normalize(b, axis=1, norm='l1')
        return size
    ############################################################################################
    #Fallunterscheidung
    ############################################################################################
    if rho_dichte is not None:
        if par_dichte is not None:
            if ax_par1 is not None:
            #Fall 1
                for rho_class in range(len(rho_dichte)):
                    rho = rho_dichte[rho_class]
                    size= laengsverteilung(size,rho, rho_class)
                #return size  
            else:
            # Fall 5
                size = vertical_simplifcation(ncol,npartype,rho_dichte,par_dichte,poroclass,sizeclass)
                
        else:
            if ax_par1 is not None:
            # Fall 2
                par_dichte = np.ones(len(rho_dichte))
                size= laengsverteilung(size) 
                size= size*rho_dichte
            else:
            # Fall 6
                size = vertical_simplifcation(ncol,npartype,rho_dichte=rho_dichte,poroclass=poroclass)
                
    else:
        if par_dichte is not None:
            if ax_par1 is not None:
            # Fall 3
                size= laengsverteilung(size)
                
            else:
            # Fall 7
                size = vertical_simplifcation(ncol,npartype,par_dichte=par_dichte,sizeclass=sizeclass)
                
        else:
            if ax_par1  is not None:
            # Fall 4
                raise Exception('kein Möglicher Fall')
                print('Physikalisch nicht möglicher Fall')
            else:
            # Fall 8
                size=[1]
                print('Homogener Fall')
                
#     checksum = np.sum(size, axis=1)
#     for i in range(len(checksum)):
#         if checksum[i] != 1:
#             size[i]=size[i]/checksum[i]    
#         if npartype == 1 :
#             size = 1
#     if size = 1:
#         size=size
#     else:
    size = np.nan_to_num(size)
    if len(size) !=1:
        size=normalize(size, axis=1, norm='l1')
    size=size.flatten()
    size=size.tolist()
    return size #, checksum
    
def CADETInputs(ncol, size_distribution=None, porosity_distribution=None, axial_distribution=None):
    if size_distribution is not None:
        if 'Frank' in size_distribution:    
            sizeclass=[0.63,1,1.4,2]
        elif 'Ruhl' in size_distribution:    
            sizeclass=[0.6,1,1.4,2]
        size_fit = preprocessing(size_distribution,ncol,sizeclass)
        size = forvolfrac(size_fit,size_distribution, sizeclass)
        size_npartype=len(size)
        
    else:
        size=None
        size_npartype=1
        sizeclass= [1.1]
    if porosity_distribution is not None:
        poro_classsize=[0.3,0.5,0.6,0.8]
        poro_fit = preprocessing(porosity_distribution,ncol,poro_classsize)
        porosity = forvolfrac(poro_fit,porosity_distribution,poro_classsize)
        porosity_npartype=len(porosity)
        
    else:
        porosity=None
        porosity_npartype=1
        poro_classsize= [0.555]
    if axial_distribution is not None:
        axial_fit = preprocessing(axial_distribution,ncol)
    else:
        axial_fit=None
    npartype=porosity_npartype*size_npartype
    
    size_for_cadet = []
    for k in range(len(sizeclass)):
        if k ==0:
            size_for_cadet.append(sizeclass[k]/2)
        else:
            size_for_cadet.append((sizeclass[k-1]+sizeclass[k])/2)
    if len(sizeclass)==1: 
        size_for_cadet=sizeclass
        
    porosity_for_cadet = []
    for k in range(len(poro_classsize)):
        if k ==0:
            porosity_for_cadet.append(poro_classsize[k]/2)
        else:
            porosity_for_cadet.append((poro_classsize[k-1]+poro_classsize[k])/2)
    if len(poro_classsize)==1: 
        porosity_for_cadet=poro_classsize
    
    sizeclasses=[]
    #if size_npartype != 1:
    for i in range(porosity_npartype):
        for j in range(size_npartype):
            sizeclasses.append(size_for_cadet[j])
    porosityclasses = []
    #if porosity_npartype != 1:
    for i in range(porosity_npartype):
        for j in range(size_npartype):
            porosityclasses.append(porosity_for_cadet[i])
                
    vol_frac=vol_frac_input(ncol,npartype,rho_dichte=porosity,par_dichte=size,ax_par1=axial_fit,ax_distr=axial_fit,poroclass=porosityclasses, sizeclass=sizeclasses)
    
    sizeclasses= np.array(sizeclasses)/2000
    sizeclasses= sizeclasses.tolist()
    return vol_frac , sizeclasses, porosityclasses ,npartype
